# Project 3: Reddit API Classification & Natural Language Processing

## Tom Ludlow, DSI-NY-6

Using NLP to identify posts from **r/audioengineering** and **r/livesound**

# Notebook 2: Pre-Processing

In [88]:
# library imports
import requests
import time
import pandas as pd
import numpy as np
import ast
import re
from tqdm import tqdm

# preprocessing imports
from nltk.tokenize import RegexpTokenizer
from nltk.stem import WordNetLemmatizer
from nltk.stem.porter import PorterStemmer
from sklearn.model_selection import train_test_split

In [89]:
# random state var
r = 1219

## Pre-processing

Reimport our post DataFrame to begin pre-processing.

In [90]:
df = pd.read_csv('./csv/181219_post_df.csv')

In [19]:
df.shape

(1904, 6)

In [20]:
df.comb.head(30)

0     Tech Support and Troubleshooting - December 10...
1     Gear Recommendation (What Should I Buy?) Threa...
2     Will I EVER understand compression...? Ahh yes...
3     I'm interviewing to be an intern at a big stud...
4     If I faced two speakers towards each other, on...
5     How to get vox to "sit" in the mix? I keep get...
6     Rode NTA-1 Capsule Swap? Hey everyone,\n\nI've...
7     Ever used Spectra Sonics? The 610 and v610 wer...
8     Live Mixing Simulator Is there such a thing as...
9     Making a guitar amp I am looking into making m...
10    How wide should a shockmount be for AT2020 XLR...
11    How do I know when a single sound is spectrall...
12    Any FUN books you could recommend as gifts? My...
13    Help for a total beginner (Increasing inputs t...
14    Friday - How did they do that? - December 14, ...
15    The most insane/bizarre source of random noise...
16    EQ before or after the compressor? I’ve seen i...
17    Can someone help explain these drivers? Ba

In [21]:
df.head()

title  \
0  Tech Support and Troubleshooting - December 10...   
1  Gear Recommendation (What Should I Buy?) Threa...   
2             Will I EVER understand compression...?   
3  I'm interviewing to be an intern at a big stud...   
4  If I faced two speakers towards each other, on...   

                                                post       author  upvotes  \
0  Welcome the /r/audioengineering Tech Support a...     t2_6l4z3        7   
1  Welcome to our weekly Gear Recommendation Thre...     t2_6l4z3       15   
2  Ahh yes, my monthly compression post...\n\nI '...  t2_2r3uhjqr       96   
3  What questions should I ask?\n\nEdit: I'm gett...     t2_dd3qi      145   
4                                                        t2_bl2x2        5   

   is_ls                                               comb  
0      0  Tech Support and Troubleshooting - December 10...  
1      0  Gear Recommendation (What Should I Buy?) Threa...  
2      0  Will I EVER understand compression...? Ahh yes...  
3      0  I'm interviewing to be an intern at a big stud...  
4      0  If I faced two speakers towards each other, on...

### Tokenizing titles and posts

We begin by tokenizing our posts, which we will do using Regex (regular expression) formatting.  Our target result is to collect any full words from our post strings, as well as any words connected by a single `/`, in order to maintain URL connection.

In [22]:
rt = RegexpTokenizer(r"[\w/\']+") # regex to include words, slash characters for urls, apostrophes

To test our Regex formatting, we will use this sample text pasted into the Regex101.com tool.

In [23]:
df.comb.sample(30)

384     OTT on every track ? Hello everyone , i want t...
1891    I have a home studio, and solid recording equi...
836     Trying to pan guitars left/right. How much % s...
79      Is There a way to mimic dan dugan automixer wi...
482     Stereo imaging in reference to mixing X POST F...
1639    Going for a Stagehand job, but I'm not extreme...
1627    X32 Rack - can you send multiple backing track...
1800    Can I use a Sennheiser EWG3 instrument transmi...
275     What can I do to cut out crackling/popping fro...
438     Zoom wsu-1 windscreen—good for singing? Audio ...
1225    SD10 and DigiRack compatibility Hi friends. I ...
255     How do you guys deal with 808/Kick Balance? Th...
612     Does Manhattan/parallel compression create a s...
95      Recording ac. guitar with a combo of large and...
496     Recording line-level with a Berhinger UMC204HD...
486     Best Free File Sharing? Does anyone have a rec...
681     Any good channels/websites to learn audio engi...
281     Tips &

There are a number of HTML-formatted character values that were captured during our API pulls.  We remove them manually through an enumerated loop.

In [48]:
for i, text in enumerate(df.comb): # for each string in our combined column
    text_loop = text.replace('&amp;','&')
    text_loop = text_loop.replace('#x200B;',' ') # manually remove symbols &, nzsp, nbsp, \n
    text_loop = text_loop.replace('nbsp;',' ')
    df.comb.iloc[i] = text_loop.replace('\n',' ').strip()
    

In [49]:
len(df.comb)

1904

#### Tokenize each post and save to list

In [59]:
comb_tokens = []  # empty token list

for i in range(len(df.comb)):
    loop_tokens = rt.tokenize(df.comb.iloc[i].lower()) # use iloc to skip removed rows
    for j, token in enumerate(loop_tokens):
        if re.match(r"\d+[\w]*", token):
            loop_tokens[j] = ''
        if re.match(r"//[\w]*", token):
            loop_tokens[j] = ''
        if ('audioengineering' in token)|('livesound' in token)|('http' in token):
            loop_tokens[j] = ''
    comb_tokens.append(loop_tokens)                    # add tokenized string to post_tokens list

In [60]:
comb_tokens[:2]

[['tech',
  'support',
  'and',
  'troubleshooting',
  'december',
  '',
  '',
  'welcome',
  'the',
  '',
  'tech',
  'support',
  'and',
  'troubleshooting',
  'thread',
  'we',
  'kindly',
  'ask',
  'that',
  'all',
  'tech',
  'support',
  'questions',
  'and',
  'basic',
  'troubleshooting',
  'questions',
  'how',
  'do',
  'i',
  'hook',
  'up',
  "'a'",
  'to',
  "'b'",
  'headphones',
  'vs',
  'mons',
  'etc',
  'go',
  'here',
  'if',
  'you',
  'see',
  'posts',
  'that',
  'belong',
  'here',
  'please',
  'report',
  'them',
  'to',
  'help',
  'us',
  'get',
  'to',
  'them',
  'in',
  'a',
  'timely',
  'manner',
  'thank',
  'you',
  'daily',
  'threads',
  'monday',
  'gear',
  'recommendations',
  'sticky',
  'thread',
  '',
  '',
  'reddit',
  '',
  'q',
  'title',
  '',
  'author',
  '',
  'restrict_sr',
  'on',
  'sort',
  'new',
  't',
  'all',
  'monday',
  'tech',
  'support',
  'and',
  'troubleshooting',
  'sticky',
  'thread',
  '',
  '',
  'reddit',
  '',


## Stem tokens

We will improve the modeling ability of our strings by using a stemmer, which trims characters from each word to convert it to a stem.  Words will register as equivalent during feature extraction if they share a stem (i.e., `computer`,`computing`,`computed` all result in a stem of `comput`).

We will use the `PorterStemmer` class from the `nltk` library.

In [61]:
ps = PorterStemmer()

In [62]:
posts_t_st = [] # posts tokenized stemmed

for post in comb_tokens:
    post_st = [] # empty post stems
    for word in post:
        print(word)
        word_st = ps.stem(word) # get stem of word
        post_st.append(word_st) # add to post list
    posts_t_st.append(post_st)  # add post list to stem matrix

tech
support
and
troubleshooting
december


welcome
the

tech
support
and
troubleshooting
thread
we
kindly
ask
that
all
tech
support
questions
and
basic
troubleshooting
questions
how
do
i
hook
up
'a'
to
'b'
headphones
vs
mons
etc
go
here
if
you
see
posts
that
belong
here
please
report
them
to
help
us
get
to
them
in
a
timely
manner
thank
you
daily
threads
monday
gear
recommendations
sticky
thread


reddit

q
title

author

restrict_sr
on
sort
new
t
all
monday
tech
support
and
troubleshooting
sticky
thread


reddit

q
title

author

restrict_sr
on
sort
new
t
all
tuesday
tips
tricks


reddit

q
title



and


or
author


restrict_sr
on
sort
new
t
all
friday
how
did
they
do
that


reddit

q
title

author

restrict_sr
on
sort
new
t
all
gear
recommendation
what
should
i
buy
thread
december


welcome
to
our
weekly
gear
recommendation
thread
where
you
can
ask

for
recommendations
on
smart
purchases
low
cost
gear
and
purchasing
recommendation
requests
have
become
common
in
the
ae
subreddit
ther

price
range
b
marginal
benefit
decreases
so
there's
no
point
in
improving
audio
quality
if
most
buyers
won't
notice
a
difference
when
using
eq
on
dialogue
does
subtle
work
or
is
it
necessary
to
make
strong
corrections
i
eq
dialogue
and
i
usually
make
very
subtle
cuts
and
boosts
no
more
than

can
the
average
listener
actually
hear
this
or
am
i
wasting
my
time
why
do
guitar
amp
manufacturers
advertise
about
how
great
their
amps'
bass
frequency
response
is
it's
relatively
common
for
guitar
amps
to
be
advertised
using
phrases
like
huge
monstrous
bass
and
other
marketing
terms
regarding
the
impressiveness
of
how
bass
frequencies
are
reproduced
by
the
amp
is
this
a
mere
marketing
gimmick
oriented
toward
guitar
players
who
either
don't
know
or
don't
care
how
the
amount
of
bass
in
their
tone
might
interact
negatively
with
the
tone
of
the
band's
bassist
when
guitar
amp
manufacturers
advertise
how
great
the
bass
response
of
their
amp
is
are
they
also
necessarily
referring
to
the
extent
to
which


room
in
room
construction
the
idea
is
basically
to
record
our
band
on
multiple
tracks
while
jamming
or
rehearsing
and
for
the
producers
to
have
a
somewhat
nice
sounding
room
while
being
able
to
record
external
musicians
it
s
a
basement
room
of
ca

with
tapestry
and
plasterboard
walls
and
ceiling
since
none
of
us
has
ever
done
this
before
we
don
t
know
what
s
best
for
the
room
has
anyone
experience
with
an
opened
control
room
like
this
should
we
stick
to
the
live
end
dead
end
principle
i
m
very
excited
about
this
and
would
be
happy
to
hear
what
you
guys
think
anyone
successfully
rocking
hackintosh
as
their
primary
machine
for
mixing/tracking/production
in
a
professional
environment
anyone
successfully
rocking
hackintosh
as
their
primary
machine
for
mixing/tracking/production
in
a
professional
environment
i
tried
it
once
upon
a
time

and
concluded
that
it
was
too
risky
has
it
gotten
any
better
in
recent
years
specifically
if
there's
anyone
who
trusts
a
hackintosh
for
their
day
to
day
rig

behringer
epa900
are
top
tier
engineers
/
producers
accessible
i
m
taking
a
class
next
quarter
which
has
a
requirement
that
i
interview
a
successful
industry
professional
i
know
a
handful
of
very
successful
performers
but
i
m
studying
music
production
so
i
thought
it
would
be
more
valuable
to
interview
a
producer
or
engineer
i
thought
i
d
throw
some
hail
mary
s
to
producers
and
engineers
from
some
of
my
favorite
albums
i
e
mitchell
froom
and
tchad
blake
in
hopes
that
they
may
be
willing
to
sit
for
an
interview
or
answer
a
few
questions
via
e
mail
however
i
can
t
seem
to
find
any
websites
or
contact
information
for
any
of
them
i
kind
of
expected
that
they
would
all
have
websites
where
i
could
at
least
send
an
inquiry
even
if
it
s
ignored
am
i
underestimating
the
celebrity
status
of
grammy
winning
engineers
and
producers
am
i
doing
the
equivalent
of
asking
taylor
swift
for
an
interview
or
are
they
just
so
embedded
into
the
industry
that
people
who
need
to
know
how
to
contact
them
know
ho

everything
should
all
single
driver
speakers
be
equally
useful
for
mix
checking
hoping
not
as
much
for
purchase
advice
as
i
am
hoping
for
discussion
about
what
makes
a
good
mix
checker
single
driver
speaker
this
way
this
thread
could
be
informative
for
many
people
people
with
more
experience
than
me
most
of
you
i'm
guessing
please
chime
in
by
single
driver
i
mean
just
a
woofer
no
tweeter
no
crossover
it
can
be
in
mono
or
stereo
or
surround
but
the
third
seems
unlikely
i
haven't
found
much
factual
information
about
the
utility
of
various
such
speakers
just
people
saying
this
is
good
buy
it
with
my
amazon
affiliate
link
so
i
get
money
i've
seen
the
occasional
post
about
this
topic
on
here
some
people
say
why
use
a
mix
cube
when
you
can
just
buy
some
of
the
top
rated
computer
speakers
from
amazon
the
top

are
all
under

and
that
mix
cubes
etc
are
a
relic
of
the
past
since
they
are
closer
to
pa
systems
which
aren't
one
of
the
primary
music
playback
forms
today
others
say
these
pro
audio
sp

...

can't
have
samples
play
back
in
sampleone
without
holding
the
freaking
button
so
i
turned
to
ableton
and
you
can
have
samples
playback
with
one
button
press
but
my
next
problem
was
getting
multiple
different
samples
not
transposed
from
the
same
dumb
sample
on
the
same
patch
correct
me
if
that's
wrong
terminology
please
i
got
an
ipad
because
i
was
told
by
multiple
people
i
could
do
what
i
needed
to
without
a
macbook
then
i
learn
that
mainstage
is
a
mac
only
app
so
i
turn
to
garageband
i
cannot
find
any
useful
tutorials
for
the
ipad
version
and
assigning
samples
to
certain
ranges
on
the
keyboard
or
even
splitting
two
different
presets
on
the
same
keyboard
for
that
matter
i
tried
kaspar
because
in
the
manual
it
stated
it
could
do
sampling
however
somethingsomething
lfos
stuff
and
it
can't
sample
nor
can
i
seem
to
get
the
sampler
in
garageband
to
send
stuff
to
kaspar
so
i
can
play
it
through
there
my
only
next
thought
is
to
partition
a
hdd
and
get
whatever
mac
os
to
run
mainstage
are
there

of
concerts
and
monitoring
myself
and
my
bandmates
as
a
performer
playing
on
stage
at
these
venues
later
this
year
i
have
noticed
one
of
the
long
term
musicians
in
the
scene
wearing
what
appear
to
be
custom
made
ear
plugs
that
he
has
around
his
neck
on
a
string
that
he
wears
at
concerts
i
can
only
presume
that
they
are
built
in
such
a
way
that
he
can
still
almost
fully
enjoy
the
music
at
shows
and
hear
what
he
needs
to
hear
while
protecting
his
hearing
does
anyone
here
have
any
advice
they
could
give
me
on
such
types
of
ear
plugs
i
imagine
i
might
need
to
see
an
audiologist
for
these
if
they
exist
and
they
will
cost
in
the

but
i'm
definitely
willing
to
spend
say


on
something
like
this
if
can
potentially
preserve
my
hearing
and
let
me
keep
playing
and
listening
to
music
for
the
rest
of
my
life
questions
about
custom
ear
plugs
and/or
iems
while
performing
my
understanding
at
the
moment
is
that
some
sort
of
wireless
iem
system
would
be
the
way
to
go
for
protecting
my
ears
yet
still
bei

pretty
decent
difference
in
bleed
and
they
are
under
the
same
exact
processing
and
at
the
same
level
both
of
them
are
very
strong
and
well
trained
singers
if
not
the
singer
on
the
wireless
is
stronger
has
anyone
else
discovered
this
or
am
i
just
dumb
and
am
hearing
things
presonus
studio
live

digital
mixer
or
apollo
twin
mkii
ok
so
i
m
in
search
of
some
upgrades
to
my
home
studio
and
i
m
torn
between
buying
a
better
audio
interface
or
buying
a
digital
mixing
console
i
have
a
neumann
tlm

and
a
twinfinity
pre
amp
with
a
m
audio
interface
my
biggest
problem
is
latency
and
i
m
wondering
if
maybe
i
should
buy
a
new
interface
or
switch
to
a
mixing
console
please
help
panicked
event
coordinator
comes
up
to
you

mins
before
doors
and
says
you
ve
got
some
music
you
can
play
right
i
ve
got
nothing
wrong
with
playing
walk
in
and
walk
out
music
however
lately
i
ve
felt
that
clients
almost
try
and
take
advantage
of
my
services
i
had
a
client
complain
that
my
music
i
selected
wasn
t
peppy
enough
s

set
is
mic'd
and
every
time
they
hit
the
symbol
it
feels
like
my
ear
drums
are
going
to
blow
oh
and
i'm


feet
from
them
conference
walk
up/out
music
does
anyone
have
a
good
spotify
playlist
with
a
bunch
of
options
or
any
artists/songs
i
can
download
to
a
playlist
run
into
this
all
the
time
and
am
always
scrambling
looking
for
upbeat
mostly
instrumental
or
minimal
words
thanks
i
have
a
home
studio
and
solid
recording
equipment
but
that
s
not
useful
for
live
audio
right
i
ve
built
up
a
nice
home
studio
with
two
solid
and
reliable
mics
i
have
loads
of
software
plugins
and
have
songs
mixed
but
those
recording
mics
condenser
those
software
plugins
it
s
all
fairly
useless
in
a
live
setting
right
in
a
live
audio
setting
how
much
software
do
you
guys
actually
use
and
do
you
use
third
part
plugins
which
would
likely
introduce
latency
or
do
you
stick
almost
entirely
to
hardware
what
are
the
essentials
for
a
recording
artist
to
understand
and
can
anything
aside
from
basic
cables
be
brought
into


i
think
next
time
i
ll
try
to
get
everyone
on
pickups
and
do
a
couple

s
in
an
xy
config
on
one
stand
so
they
can
still
feel
like
they
re
around
the
mic
is
this
a
good
approach
any
suggestions
are
welcome
cheapest


channel
mixers
with
compressors
i've
been
considering
the
presonus
studiolive
despite
bad
reviews
because
i
can't
spend
over

edit
can't
do
the
ipad
controlled
option
unfortunately
do
i
need
an
interface
with
an
x32
so
i
m
a
volunteer
at
my
local
church
on
the
sound
board
so
i
m
very
very
new
at
the
sound
thing
we
are
thinking
of
live
streaming
our
services
and
i
m
wondering
do
i
need
an
interface
to
do
this
we
have
a
behringer
x32
and
i
cannot
find
anything
that
says
i
do
need
or
do
not
need
an
interface
i
am
wondering
if
anyone
has
experience
with
this
and
knows
what
i
might
need
to
set
up
the
sound
from
the
board
to
the
live
streaming
software
bass
head
directly
into
pa
my
church
is
in
the
middle
of
a
new
building
and
new
equipment
to
accompany
it
they
insist
on
skipping

### Combine stems to single string list

In [63]:
# format tokenized stems for vectorizer: list of strings
posts_t_st_list = []

for post in posts_t_st:
    posts_t_st_list.append(' '.join(post))

## Lemmatized tokens

We will try Lemmatizing as well, which is a "lighter-touch" approach.  We can run both vectors through our initial models to determine which is better.

We used the `WordNetLemmatizer` class from the `nltk` library.

In [64]:
lm = WordNetLemmatizer()

In [65]:
posts_t_lm = []

for post in comb_tokens:
    post_st = [] # empty post stems
    for word in post:
        print(word)
        word_st = lm.lemmatize(word) # get lemmatized word
        post_st.append(word_st) # add to post list
    posts_t_lm.append(post_st)  # add post list to lemma matrix

tech
support
and
troubleshooting
december


welcome
the

tech
support
and
troubleshooting
thread
we
kindly
ask
that
all
tech
support
questions
and
basic
troubleshooting
questions
how
do
i
hook
up
'a'
to
'b'
headphones
vs
mons
etc
go
here
if
you
see
posts
that
belong
here
please
report
them
to
help
us
get
to
them
in
a
timely
manner
thank
you
daily
threads
monday
gear
recommendations
sticky
thread


reddit

q
title

author

restrict_sr
on
sort
new
t
all
monday
tech
support
and
troubleshooting
sticky
thread


reddit

q
title

author

restrict_sr
on
sort
new
t
all
tuesday
tips
tricks


reddit

q
title



and


or
author


restrict_sr
on
sort
new
t
all
friday
how
did
they
do
that


reddit

q
title

author

restrict_sr
on
sort
new
t
all
gear
recommendation
what
should
i
buy
thread
december


welcome
to
our
weekly
gear
recommendation
thread
where
you
can
ask

for
recommendations
on
smart
purchases
low
cost
gear
and
purchasing
recommendation
requests
have
become
common
in
the
ae
subreddit
ther

there
with
the
peak
being
around

on
the
levels
my
issue
is
that
it's
a
very
dense
mix
with
a
punk
rock
vibe
low
end
rumble
taken
out
all
the
high
end
that
wasn't
audible
in
the
mix
shelved
off
i've
done
everything
i
can
to
make
sure
everything
is
audible
and
i'm
happy
with
how
it's
sounding
but
it's
just
too
quiet
relative
to
everything
else
on
the
platform
the
only
option
i
can
see
is
to
turn
the
limiter
gain
up
but
that
will
compromise
the
mix
which
i'm
happy
with
what
do
i
do
edit
thank
you
to
everyone
that
chimed
in
it's
been
a
really
useful
learning
experience
is
there
a
free
calculator
for
determining
the
subjective
tone
from

frequency
waves
link
to
what
i'm
talking
about


phy
astr
gsu
edu/hbase/sound/subton
html
c1
essentially
i
want
to
be
able
to
put
in
f1
f2
fn
and
phases
as
percents
for
each
wave
and
get
a
list
of
subjective
tones
with
beat
and
frequency
information
i've
tried
google
but
could
only
find
above
resource
which
bass
trap
design
should
i
choose
if
i
am
using

r

you
could
build
a
floor
plan
and
designate
a
spot
where
the
audio
source
is
coming
from
and
the
program
would
calculate
the
room
things
in
the
room
and
the
walls
then
it
would
apply
the
effects
to
make
the
sound
fit
the
setting
e
g
reverb
eq
amplify
ect
say
there
was
a
narrator
and
you
wanted
him
to
sound
like
he
was
sitting
next
to
or
moving
around
you
and
your
both
in
a
church
with
the
program
you
could
build
the
floor
plan
of
the
church
and
program
the
path
of
the
voice
then
the
program
would
calculate
the
distance
of
the
voice
to
apply
any
amplification
and
if
your
subject
walks
around
a
wall
the
program
would
calculate
the
thickness
and
material
of
the
wall
and
change
the
voice
to
match
what
it
would
accurately
sound
like
is
this
a
thing
already
and
if
it's
not
why
not
using
a
single
reverb/delay
on
all
parts
in
a
mix
i've
toyed
with
this
idea
for
a
little
while
but
finally
gone
through
with
it
i
set
up
my
latest
mixing
project
so
that
all
of
the
individual
components
of
the
track

as
we
don
t
really
do
sound
checks
longer
than
a
moment
to
get
just
the
level
tonight
i
finally
got
rid
of
it
by
simply
scooping
out
a
whole
lot
around

and
i
m
stoked
exactly
what
i
ve
been
looking
to
get
rid
of
vox
sound
so
much
smoother
and
less
offensive
to
the
ear
seems
like
such
an
obvious
simple
fix
now
that
i
found
it
i
ve
definitely
just
been
too
conservative
about
cutting
in
that
range
in
the
past
i
ve
been
questioning
lately
if
my
ears
are
just
super
sensitive
to
high
freq
because
i
work
with
other
sound
techs
who
don
t
seem
to
be
bothered
by
sibilance/
bitey
freq
to
the
degree
i
am
when
they
mix
i
believe
that
i
am
extra
sensitive
to
it
because
i
even
notice
it
in
a
lot
of
professionally
recorded/
mastered
tracks
to
a
lesser
degree
than
live
music
i
take
good
care
of
my
ears
wear
my
molds
after
i
get
the
mix
dialed
in/take
frequent
breaks
when
i
m
mixing
recordings
anyway
this
is
all
just
to
say
i
m
excited
about
my
realization
and
to
remind
my
fellow
aspiring
engineers
to


ram
to

if
it's
an
issue
with
sony
acid
whats
an
easy
program
i
can
learn
without
much
training
basically
i'm
looking
to
fix
these
problems
without
spending
much
more
money
good
enough
is
good
enough
but
if
my
preamp
mic
program
or
a
combination
of
them
is
causing
the
volume
problems
and
lag
how
can
i
fix
it
cheaply
thanks
in
advance
looking
for
the
ultimate
calculation
site
hey
guys
i
know
there
are
a
lot
of
sites
out
there
but
i
was
wondering
if
there
is
a
site
where
you
can
enter
bpm/sample
rate
and
it
gives
you
all
note
lengths
gt

in
miliseconds
and
hz
as
well
as
their
respective
sample
sizes
i'm
tired
of
using
multiple
it
can
be
very
time
consuming
thank
you
in
advance
any
way
to
add
chapter
markers
to
file
during
recording
i
hope
this
is
the
right
place
for
this
question
tl
dr
i
want
to
add
chapter
markers
to
a
file
while
i
am
recording
it
solution
needs
to
work
in
a
windows
environment
and
i
need
to
be
able
to
create
the
chapter
markers
via
command
line
i
don't
care
what
the
fi

...

playing
butt
rock
but
it
was
nice
to
hear
the
appreciation
hell
imho
their
tunes
were
pretty
bad
but
i
was
happy
to
help
monitors
them
do
their
thing
c'est
la
vie
first
time
running
front
of
house
sound
last
night
was
a
simple
set
up
using
a
yamaha
tf
rack
on
stage
controlled
by
an
ipad
anyone
else
using
the
shure
vhf
wireless
lots
of
issues
here
we
transitioned
to
the
shure
ulx
d
vhf
v50

to

and
have
been
having
a
lot
of
issues
lots
of
interference
preacher
is
only
about

feet
away
no
walls
blocking
turned
the
transmitter
up
to
hi

can't
seem
to
get
a
good
clean
signal
compared
to
our
old

sennheiser
equipment
anyone
else
using
these
maybe
we
need
to
get
a
directional
antenna
but
i'm
tempted
to
tell
them
to
return
it
pay
scale
for
your
market
hey
everyone
so
i
m
curious
about
what
our
scales
are
like
in
certain
markets
where
i
m
at
city
of
about


rates
are
about


with

to
someone
with
decent
experience
and

for
a1
level
work
what
are
scales
looking
like
in
your
market
stupidest
thi



i
will
do
the
setup
and
soundcheck
early
in
the
afternoon
but
for
this
type
of
event
want
someone
there
to
mix
while
we
play
i'm
reaching
out
here
because
the
band
is
from
philly
and
with
the
budget
i
have
for
a
tech
i
feel
bad
asking
someone
to
make
that
long
commute
the
gig
is
in
westminster
md
on

i
can
pay

for

hours
dinner
if
you
come
at

when
the
band
eats
i
know
it's
not
a
lot
of
but
all
you'd
be
responsible
for
is
mixing
for
those

hours
which
include
a
short
set
break
if
you
live
in
the
area
this
is
a
cake
gig
system
is
behringer
xr18
we'll
have
a
dedicated
ipad
for
you
or
you
can
bring
your
laptop
speakers
are
ev
zlx
series

subs

tops

monitor
mixes
a
few
of
us
on
ears
band
will
set
up
and
check
before
the
ceremony
so
it's
basically
a
babysitting
gig
thanks
and
be
well
advice
on
amplifying
a
dulcimer
hi
there
i
ve
been
asked
about
possible
solutions
for
amplifying
the
sound
of
a
dulcimer
live
has
anyone
got
any
recommendations
on
good
pick
ups
or
mics
best
low
price/best


i
can
see
that
i'll
pick
it
up
very
quickly
if
i
keep
up
good
work
ethic
and
going
the
extra
mile
how
soon
would
a
transfer
to
a
different
property
be
possible
i'm
trying
to
be
closer
to
my
family
and
partner
wireless
beta87a
more
bleed
than
wired
beta

i
was
mixing
my
church's
livestream
and
a
weird
thing
i
noticed
is
that
the
wireless
mic
has
more
drum/cymbal
bleed
than
the
wired
mic
now
what
makes
this
weird
is
a
few
things

they
are
both
extremely
similar
capsules
the
wireless
mic
is
a
shure
ulx2
beta

so
this
is
a
condenser
and
hypercardioid
the
wired
mic
is
a
beta

same
idea
but
a
cardioid
microphone

the
wireless
mic
singer
is
about

feet
further
away
from
the
drums
than
the
main
singer
on
the
wired
mic
wired
microphone
in
the
center
wireless
on
right
and
left
drums
in
the
back
right
corner
of
the
stage
and
this
wireless
in
question
in
in
the
front
left
of
the
stage
there's
a
pretty
decent
difference
in
bleed
and
they
are
under
the
same
exact
processing
and
at
the
same
level
bot

in

early

i
interned
at
an
audio
mastering
and
restoration
studio
and
from
the
first
half
of

to
the
end
of
june

i
stacked
boxes
in
trucks
at
amazon


hours
per
day
no
other
job
prospects
i
interviewed
in
early
spring
with
a
big
av
company
who
seemed
interested
and
then
didn't
give
me
the
job
because
the
only
work
i'd
done
was
studio
work
and
some
rigging
i
started
with
my
current
company
july

it
was
really
new
and
exciting
for
a
couple
weeks
then
the
lead
technician
quit
and
left
me
with
the
only
other
tech
he
can
setup
equipment
really
quick
but
it
can
take
him


times
as
long
as
i
do
to
scan
an
order
and
fill
it
or
receive
it
he's
an
older
guy
and
doesn't
know
much
about
computers
of
powerpoint
so
i'm
stuck
dealing
with
all
of
that
bullshit
before
presentations
our
biggest
account
had
us
come
to
a
hotel
and
run
a
conference
the
sales
and
banquet
staff
didn't
look
at
the
setup
diagrams
and
moved
his
tables
from
where
they
were
supposed
to
be
and
he
chewed
me
out
for
it
he
was
upse

is
really
throwing
me
off
so
any
insight
would
be
appreciated
post
game
update
we
had
our
rehearsal
friday
with
the
choir
and
our
biggest
issue
was
feedback
we
initially
had


out
but
cut
it
down
to

after
the
feedback
issues
their
final
position
was
a
little
below
chest
height
pointed
ever
so
slightly
upwards
there
were
no
problems
when
the
band
was
playing
quietly
but
as
soon
as
they
started
to
step
on
the
gas
we
were
hitting
major
feedback
very
quickly
we
pinpointed
the
feedback
to
surprise
the
drumline
and
specifically
bass

was
tuned
to
the
same
pitch
that
kept
amplifying
itself
so
we
took
that
bass
out
of
the
show
and
eq'd
out
as
much
of
the
bass
as
possible
on
our
mixer
overall
everything
worked
there
were
only
a
couple
moments
during
the
show
feedback
started
to
creep
in
but
we
kept
it
all
under
control
looking
back
i
really
wish
i
had
a
drum
shield
will
probably
make
this
investment
the
next
time
we
have
a
choir
and
an
equalizer
i've
been
looking
at
the
behringer
fbq3102hd
gra

### Combine lemmatized to list

In [66]:
posts_t_lm_list = []

for post in posts_t_lm:
    posts_t_lm_list.append(' '.join(post))

In [67]:
posts_t_lm_list[:2]

["tech support and troubleshooting december   welcome the  tech support and troubleshooting thread we kindly ask that all tech support question and basic troubleshooting question how do i hook up 'a' to 'b' headphone v mon etc go here if you see post that belong here please report them to help u get to them in a timely manner thank you daily thread monday gear recommendation sticky thread   reddit  q title  author  restrict_sr on sort new t all monday tech support and troubleshooting sticky thread   reddit  q title  author  restrict_sr on sort new t all tuesday tip trick   reddit  q title    and   or author   restrict_sr on sort new t all friday how did they do that   reddit  q title  author  restrict_sr on sort new t all",
 'gear recommendation what should i buy thread december   welcome to our weekly gear recommendation thread where you can ask  for recommendation on smart purchase low cost gear and purchasing recommendation request have become common in the ae subreddit there is als

### Add index to posts and titles and create DataFrames

Here we create a DataFrame with our combined posts with both stem and lemmatized values, and save to csv to continue.

In [68]:
df_pre = pd.DataFrame(data=[posts_t_st_list, posts_t_lm_list], index=['post_st','post_lm'])

In [69]:
df_pre = df_pre.T

In [70]:
df_pre.head()

post_st  \
0  tech support and troubleshoot decemb   welcom ...   
1  gear recommend what should i buy thread decemb...   
2  will i ever understand compress ahh ye my mont...   
3  i'm interview to be an intern at a big studio ...   
4  if i face two speaker toward each other one pl...   

                                             post_lm  
0  tech support and troubleshooting december   we...  
1  gear recommendation what should i buy thread d...  
2  will i ever understand compression ahh yes my ...  
3  i'm interviewing to be an intern at a big stud...  
4  if i faced two speaker towards each other one ...

In [71]:
df_pre['is_ls'] = df['is_ls']

In [72]:
df_pre.head()

post_st  \
0  tech support and troubleshoot decemb   welcom ...   
1  gear recommend what should i buy thread decemb...   
2  will i ever understand compress ahh ye my mont...   
3  i'm interview to be an intern at a big studio ...   
4  if i face two speaker toward each other one pl...   

                                             post_lm  is_ls  
0  tech support and troubleshooting december   we...      0  
1  gear recommendation what should i buy thread d...      0  
2  will i ever understand compression ahh yes my ...      0  
3  i'm interviewing to be an intern at a big stud...      0  
4  if i faced two speaker towards each other one ...      0

In [73]:
df_pre.to_csv('./csv/181220_df_pre.csv', index=False)

## Train-Test Split

We will perform a train/test split of the data, which will share index values.  This allows us to directly compare the modeling accuracy scores between stemmed and lemmatized vectors.

In [74]:
df_pre = pd.read_csv('./csv/181219_df_pre.csv') # reimport data

In [75]:
df_pre.head()

post_st  \
0  tech support and troubleshoot decemb   welcom ...   
1  gear recommend what should i buy thread decemb...   
2  will i ever understand compress ahh ye my mont...   
3  i'm interview to be an intern at a big studio ...   
4  if i face two speaker toward each other one pl...   

                                             post_lm  is_ls  
0  tech support and troubleshooting december   we...      0  
1  gear recommendation what should i buy thread d...      0  
2  will i ever understand compression ahh yes my ...      0  
3  i'm interviewing to be an intern at a big stud...      0  
4  if i faced two speaker towards each other one ...      0

In [76]:
df_pre.isnull().sum()

post_st    1
post_lm    1
is_ls      0
dtype: int64

In [77]:
df_pre.dropna(inplace=True) # remove nulls to continue

We set our `X` matrix to contain both post vectors, and our `y` target matrix to `is_ls`.

In [78]:
X = df_pre[['post_st','post_lm']]
y = df_pre['is_ls']

In [79]:
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=r, stratify=y)

We confirm that our train and test values are the same length.

In [80]:
len(X_train)

1427

In [81]:
len(X_test)

476

In [82]:
len(y_train)

1427

In [83]:
len(y_test)

476

In [84]:
y_train = pd.DataFrame(y_train, columns=['is_ls'])

In [85]:
y_test = pd.DataFrame(y_test, columns=['is_ls'])

Saved each train and test DataFrame to a separate dated csv for future reference.

In [87]:
X_train.to_csv('./csv/181220_X_train.csv', index=True)
X_test.to_csv('./csv/181220_X_test.csv', index=True)
y_train.to_csv('./csv/181220_y_train.csv', index=True)
y_test.to_csv('./csv/181220_y_test.csv', index=True)

## Continue to Notebook 3: Model Selection